In [66]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
from fredapi import Fred
import warnings
warnings.filterwarnings("ignore")


In [67]:
df = pd.read_csv("malotest.csv", sep=";", decimal=",")
df = df.rename(columns={
    "Column1":  "Date",
    "Column2":  "SXXT",
    "Column3":  "SXNT",
    "Column4":  "SX7T",
    "Column5":  "SX4T",
    "Column6":  "SXQT",
    "Column7":  "SX8T",
    "Column8":  "SXIT",
    "Column9":  "SXAT",
    "Column10": "SXDT",
    "Column11": "SXET",
    "Column12": "SX6T",
    "Column13": "SX3T",
    "Column14": "SXKT",
    "Column15": "SXOT",
    "Column16": "SXRT",
    "Column17": "SXMT",
    "Column18": "SX86T",
    "Column19": "SXPT",
    "Column20": "SXFT",
    "Column21": "SXTT"
}
)
df["Date"] = pd.to_datetime(df["Date"], format="%d/%m/%Y")

In [68]:
def GetReturn(df,date,lookback):
    date=pd.to_datetime(date)
    if date not in df["Date"].values:#add breaker if windows not in df
        raise ValueError("Date not in dataframe")
    returns_df = df[[
    "Date",
    "SXNT",
    "SX7T",
    "SX4T",
    "SXQT",
    "SX8T",
    "SXIT",
    "SXAT",
    "SXDT",
    "SXET",
    "SX6T",
    "SX3T",
    "SXKT",
    "SXOT",
    "SXRT",
    "SXMT",
    "SX86T",
    "SXPT",
    "SXFT",
    "SXTT"
]].copy()

    date_list=returns_df.drop(columns="Date")
    date_index = returns_df.index[returns_df["Date"] == date][0]
    returns_df=returns_df[(returns_df.index<=date_index) & (returns_df.index>=date_index-lookback) ]
    returns_df.drop(columns="Date",inplace=True)

    returns_df = np.log(returns_df/ returns_df.shift(1))
    returns_df.dropna(inplace=True)
    #print(returns_df.std().mean()) #verification if std is around 1% daily

    return returns_df


def GetReturnSPX(df,date,lookback):
    date=pd.to_datetime(date)
    if date not in df["Date"].values:#add breaker if windows not in df
        raise ValueError("Date not in dataframe")
    returns_df = df[["Date","SPX"]].copy()

    date_list=returns_df.drop(columns="Date")
    date_index = returns_df.index[returns_df["Date"] == date][0]
    returns_df=returns_df[(returns_df.index<=date_index) & (returns_df.index>=date_index-lookback) ]
    returns_df.drop(columns="Date",inplace=True)

    returns_df = np.log(returns_df/ returns_df.shift(1))
    returns_df.dropna(inplace=True)
    #print(returns_df.std().mean()) #verification if std is around 1% daily

    return returns_df

#Returns=GetReturn(df,"2020-05-11",lookback=180)
#ReturnsSPX=GetReturnSPX(df,"2020-05-11",lookback=180)

In [69]:
def GetSigma(df,date,lookback):
    returns_df=GetReturn(df,date,lookback=lookback)
    #covariance matric from returns_df
    sigma_windowed=returns_df.cov()

    return sigma_windowed

#Sigma=GetSigma(df,"2020-05-11",lookback=180)

In [70]:
def GetRfDataframe(df):
    fred = Fred(api_key="5c742a53d96bd3085e9199dcdb5af60b")
    riskfree = fred.get_series('DFF')
    # riskfree = fred.get_series('DTB1MO')

    riskfree = riskfree.to_frame(name='FedFunds')
    riskfree.index.name = "Date"
    riskfree = riskfree[riskfree.index >= "2002-01-01"]
    riskfree["FedFunds"]=riskfree["FedFunds"]/100
    list_days_open = pd.to_datetime(df["Date"], dayfirst=True, errors="coerce")
    list_days_full = pd.to_datetime(riskfree.index, dayfirst=True, errors="coerce")

    list_days_open=[pd.to_datetime(date) for date in list_days_open]
    list_days_full=[pd.to_datetime(date) for date in list_days_full]


    list_days_open_pondered=[]
    riskfree_list=[]
    count_list=[]
    timestamp=0
    while timestamp < len(list_days_full)-1:

      if list_days_full[timestamp+1] in list_days_open:
            list_days_open_pondered.append(list_days_full[timestamp])
            riskfree_list.append(riskfree["FedFunds"].loc[list_days_full[timestamp]])
            count_list.append(1)
            timestamp += 1

      else:
          count = 0
          timestampbis = timestamp
          while (timestamp + 1 < len(list_days_full)) and (list_days_full[timestamp + 1] not in list_days_open):
              timestamp += 1
              count += 1

          list_days_open_pondered.append(list_days_full[timestampbis])  # jour de départ
          riskfree_list.append(riskfree["FedFunds"].loc[list_days_full[timestampbis]])
          count_list.append(count+1)
          timestamp += 1

    RfDf=pd.DataFrame({"Date":list_days_open_pondered,"Rf":riskfree_list,"Count":count_list})
    RfDf=RfDf.set_index("Date")
    return RfDf

def GetRiskFree(df,date,lookback,RfDf):
    positionOfStartDate=df.index[df["Date"]==pd.to_datetime(date)][0]-lookback
    #print(positionOfStartDate)
    startDate=pd.to_datetime(df.iloc[positionOfStartDate,0])
    endDate=pd.to_datetime(date)
    RfDf=RfDf[(RfDf.index >= startDate) & (RfDf.index <= endDate )].copy()
    CumulativeRf=[]

    for i in range(len(RfDf)):
      if i==0:
        CumulativeRf.append(pow((1+RfDf["Rf"].iloc[i]),(RfDf["Count"].iloc[i]/360)))
      else:
        CumulativeRf.append(pow((1+RfDf["Rf"].iloc[i]),(RfDf["Count"].iloc[i]/360))*CumulativeRf[i-1])

    RfDf["CumulativeRf"]=CumulativeRf
    RfDf["CumulativeRf"]= RfDf["CumulativeRf"]-1

    return RfDf["CumulativeRf"].iloc[-1]

RfDf=GetRfDataframe(df)

In [71]:
def GetWeight(df,date):
    #for the moment we will use the equal weight
    weight_vector=np.zeros((df.shape[1]-2,1))
    for i in range(0,df.shape[1]-2):
        weight_vector[i]=1/(df.shape[1]-2)
    return weight_vector
print(GetWeight(df,"2020-05-11"))


[[0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]
 [0.05263158]]


In [72]:
def GetLambda(df,date,timeofcalculation,RfDf):
    returns=GetReturn(df,date,timeofcalculation)
    weight_vector=GetWeight(df,date=0)

    mean_return=np.mean(np.dot(returns,weight_vector))
    mean_annual=(1+mean_return)**252-1


    rf_temps=GetRiskFree(df,date,timeofcalculation,RfDf)
    rf_annual=(1+rf_temps)**(252/timeofcalculation)-1


    Sigma=GetSigma(df,date,timeofcalculation)
    Sigma_annual=252*Sigma
    var = float((weight_vector.T @ Sigma_annual.values @ weight_vector).item())
    print(var)
    lambda_value=(mean_annual - rf_annual)/var


    excess = mean_annual - rf_annual
    sigma2 = var
    sigma  = np.sqrt(var)
    lam    = excess / sigma2
    sharpe = excess / sigma
    print("Excess:", excess, " Var:", sigma2, " Vol:", sigma, " λ:", lam, " Sharpe:", sharpe)

    return lambda_value



Lambda=GetLambda(df,"2024-01-11",timeofcalculation=3500,RfDf=RfDf)

0.026448989139174064
Excess: 0.09161833767805083  Var: 0.026448989139174064  Vol: 0.16263145187562603  λ: 3.4639636772489464  Sharpe: 0.5633494420754286


In [73]:
def GetPMatrix(df,date, lookback,proportion=3):
    #(date)
    #print(proportion)
    #print(lookback)
    AssetColumns = ["SXNT","SX7T","SX4T","SXQT","SX8T","SXIT","SXAT","SXDT","SXET","SX6T","SX3T","SXKT","SXOT","SXRT","SXMT","SX86T","SXPT","SXFT","SXTT"]

    bestperformer = []
    performerc = []
    returnBestPerformer=[]
    returnWorstPerformer=[]

    endDateIndex=df.index[df["Date"]==pd.to_datetime(date)][0]
    startDateIndex=df.index[df["Date"]==pd.to_datetime(date)][0]-lookback

    for i in range(2, df.shape[1]):  #loop through asset columns
        performerc.append((((float(df.iloc[endDateIndex, i]) / float(df.iloc[startDateIndex, i]) - 1) * 100), i - 2,df.columns[i])) #pos of best stock in a tuple with its return

    performerc.sort(reverse=True)
    #print(performerc)
    perfMarket= (float(df.iloc[endDateIndex, 1]) / float(df.iloc[startDateIndex, 1]) - 1) * 100
    #print(f"Market performance over the period : {perfMarket}%")




    for i in range(proportion):
        bestperformer.append(performerc[i][1])
        returnBestPerformer.append(performerc[i][0])


    P=np.zeros((proportion,df.shape[1]-2))
    Q=np.zeros((proportion,1))
    for lineview in range(proportion):
        for i in range(len(AssetColumns)):
            P[lineview,i]=-1/len(AssetColumns)
        P[lineview,bestperformer[lineview]]=1-1/len(AssetColumns)

    for i in range(proportion):
        Q[i,0]=((returnBestPerformer[i]-perfMarket)/2)/100

    #print("P : ",P,"Q : ",Q)

    return P, Q
PMatrix,TempoQ=GetPMatrix(df,"2016-05-11",lookback=180,proportion=3)

In [74]:
def GetOmega(PMatrix, Sigma, c=0.5):
    #Omega is the uncertainty of the views
    factorC=(1/c-1)
    Omega=factorC*PMatrix@Sigma@np.transpose(PMatrix)


    return Omega

In [75]:
def BlackAndLittermanModel(backtestStartDate, rebalancingFrequency, lookbackPeriod, df,RfDf):
    #implement the full backtest of the black and litterman model

    #---------
    #PARAMETERS
    #---------

    free_asset=0 #proportion of risk free asset allocated in the benchmark
    taux=0.01

    Sigma=GetSigma(df,backtestStartDate,lookback=lookbackPeriod)
    Lambda=3
    PMatrix,Q= GetPMatrix(df,backtestStartDate, lookback=lookbackPeriod,proportion=3)
    Omega=GetOmega(PMatrix, Sigma, c=0.1)
    rf=GetRiskFree(df,backtestStartDate,lookbackPeriod,RfDf)
    weights = GetWeight(df, backtestStartDate)
    weights = np.array(weights).reshape(-1, 1)
    uimplied = Lambda * (Sigma @ weights) + rf
    #BL formula





    optimizedReturn=(np.linalg.inv(np.linalg.inv(taux*Sigma)+np.transpose(PMatrix)@np.linalg.inv(Omega)@PMatrix)) @ (np.linalg.inv(taux*Sigma)@uimplied+np.transpose(PMatrix)@np.linalg.inv(Omega)@Q)




    #MarkowitzAllocation
    WeightBL=np.linalg.inv(Sigma)@(optimizedReturn-rf)/Lambda

    if not np.isclose(float(np.sum(WeightBL)), 1.0, atol=1e-6):
        raise ValueError("Weights do not sum to 1, please investigate :",float(np.sum(WeightBL)))

    return WeightBL


BlackAndLittermanModel("2018-05-11", rebalancingFrequency=3, lookbackPeriod=180, df=df,RfDf=RfDf)


0
0  -0.023048
1  -0.023048
2  -0.023048
3   0.302960
4  -0.023048
5  -0.023048
6   0.966731
7  -0.023048
8  -0.023048
9  -0.023048
10 -0.023048
11 -0.023048
12 -0.023048
13 -0.023048
14 -0.023048
15 -0.023048
16 -0.023048
17 -0.023048
18  0.099080

In [81]:
from rich.console import Console
from rich.panel import Panel
from tqdm import tqdm

console = Console()

#BACK TESTER
dfbacktest=df.copy()
dfbacktest["Date"] = pd.to_datetime(df["Date"], format="%d/%m/%Y")
dfbacktest["MonthIndex"] = dfbacktest["Date"].dt.to_period("M")

df_length = dfbacktest.shape[1] - 2  # bcs of date and spx
last_rebalance = dfbacktest.loc[0, "Date"]  # première date
month_count = 0

# 🎨 AFFICHAGE STYLÉ (sans prompts)
# 🎨 AFFICHAGE STYLÉ (sans prompts)
hold = 1
hist = 0
proportion = 3

console.print(Panel.fit(
    "[bold cyan]📊 PORTFOLIO BACKTESTER[/bold cyan]\n"
    "[dim]Black-Litterman Model[/dim]",
    border_style="cyan"
))

console.print(f"\n[yellow]⚙️  Configuration :[/yellow]")
console.print(f"   • Hold period: [cyan]{hold}[/cyan] mois")
console.print(f"   • Historique: [cyan]{hist}[/cyan] mois")
console.print(f"   • Proportion: [cyan]{proportion}[/cyan]")
console.print("\n[yellow]⏳ Lancement du backtest...[/yellow]\n")

def Backtester(df,hold, hist, proportion,df_toBL, RfDf):
    print("Colonnes df AVANT drop:", df.columns.tolist())

    StockQty = df.copy()
    StockQty.drop(columns="MonthIndex", inplace=True)

    print("Colonnes StockQty APRÈS drop:", StockQty.columns.tolist())
    print(f"Boucle de 2 à {StockQty.shape[1]-1}")
    print(f"Colonnes concernées: {StockQty.columns[2:StockQty.shape[1]-1].tolist()}")

    StockQty = df.copy()
    StockQty.drop(columns="MonthIndex", inplace=True)
    start=181


    StockQty.loc[:, :] = 0
    #starting data
    MoneyAtStart = 10000000
    month_count=0
    CurrentValue=MoneyAtStart

    #first ligne
    StockQty.loc[start, "Money"] = MoneyAtStart
    StockQty.loc[start, "SXXT"] = df.iloc[start, 1]
    StockQty.loc[start, "Date"] = df.iloc[start, 0]

    #start of the algorithm

    for i in tqdm(range(start,df.shape[0]), desc="Backtesting"):
      StockQty.iloc[i,0]=df.iloc[i,0]
      StockQty.iloc[i,1]=df.iloc[i,1]
      fees=0


      if df.loc[i, "Date"].month != df.loc[i-1, "Date"].month:
        month_count += 1


    # Si on atteint la période voulue
      if i>= hist and month_count % hold == 0 and df.loc[i, "Date"].month != df.loc[i - 1, "Date"].month:
        #print(f"🔁 Rebalancement déclenché à la date : {df.loc[i, 'Date'].date()}")
        #print(str(df.iloc[i,0]))
        BLWeight=BlackAndLittermanModel(str(df.iloc[i,0]),3,3*22,df_toBL,RfDf)
        #print(len(BLWeight))
        for index in range(len(BLWeight)):
            StockQty.iloc[i,index+2]=(BLWeight.iloc[index,0]*CurrentValue)/df.iloc[i,index+2] #qty = weight*total value/price

      else :
        for stocks in range(2,StockQty.shape[1]-1):
          StockQty.iloc[i,stocks]=StockQty.iloc[i-1,stocks] #same qty
      #value of pf

      GainOrLoss = 0
      for stocks in range(2, StockQty.shape[1]-1):
          qty = StockQty.iloc[i, stocks]
          print(StockQty.columns[stocks])
          if qty != 0.0:

            price_now = df.iloc[i, stocks]
            price_prev = df.iloc[i - 1, stocks]
            print(price_now, price_prev)
            GainOrLoss += qty * (price_now - price_prev)


      CurrentValue+=GainOrLoss-fees
      StockQty.iloc[i,-1]=CurrentValue

    StockQty = StockQty.iloc[start:].reset_index(drop=True)
    return StockQty
RfDf=GetRfDataframe(df)
final = Backtester(dfbacktest, hold=hold, hist=hist, proportion=proportion, df_toBL=df,RfDf=RfDf)

console.print("\n[green]✅ Backtest terminé avec succès ![/green]\n")

╭─────────────────────────╮
│ 📊 PORTFOLIO BACKTESTER │
│ Black-Litterman Model   │
╰─────────────────────────╯

⚙️  Configuration :

• Hold period: 1 mois

• Historique: 0 mois

• Proportion: 3

...

Backtesting:  99%|█████████▉| 5550/5602 [00:27<00:00, 210.72it/s]

SXNT
4134.3 4086.31
SX7T
1189.4 1189.86
SX4T
931.5 931.65
SXQT
630.13 643.71
SX8T
779.3 779.64
SXIT
3462.14 3461.14
SXAT
3610.14 3632.36
SXDT
306.21 305.78
SXET
1805.76 1788.99
SX6T
1006.91 1005.58
SX3T
314.16 312.75
SXKT
974.9 965.31
SXOT
224.92 224.8
SXRT
112.53 111.95
SXMT
503.85 502.62
SX86T
641.13 633.29
SXPT
640.31 670.83
SXFT
808.17 803.25
SXTT
3019.61 3000.13
SXNT
4098.58 4134.3
SX7T
1188.9 1189.4
SX4T
937.35 931.5
SXQT
643.5 630.13
SX8T
779.6 779.3
SXIT
3462.65 3462.14
SXAT
3655.18 3610.14
SXDT
309.85 306.21
SXET
1798.82 1805.76
SX6T
1011.72 1006.91
SX3T
314.76 314.16
SXKT
969.68 974.9
SXOT
224.39 224.92
SXRT
112.68 112.53
SXMT
504.69 503.85
SX86T
640.58 641.13
SXPT
639.98 640.31
SXFT
801.95 808.17
SXTT
3028.56 3019.61
SXNT
4171.37 4098.58
SX7T
1194.52 1188.9
SX4T
938.19 937.35
SXQT
644.25 643.5
SX8T
780.02 779.6
SXIT
3492.21 3462.65
SXAT
3674.25 3655.18
SXDT
310.01 309.85
SXET
1809.31 1798.82
SX6T
1016.41 1011.72
SX3T
313.79 314.76
SXKT
979.74 969.68
SXOT
226.27 224.39
SXRT
1

Backtesting: 100%|██████████| 5602/5602 [00:27<00:00, 202.31it/s]

SXNT
4465.08 4399.15
SX7T
1324.44 1314.97
SX4T
1002.99 996.28
SXQT
612.33 610.09
SX8T
791.23 795.39
SXIT
3546.84 3494.55
SXAT
3974.04 3931.18
SXDT
346.3 338.31
SXET
1902.0 1917.85
SX6T
1095.12 1080.74
SX3T
309.79 310.18
SXKT
1048.11 1030.59
SXOT
243.05 240.73
SXRT
121.74 120.52
SXMT
518.55 518.02
SX86T
673.21 662.16
SXPT
720.18 719.2
SXFT
801.91 806.17
SXTT
3615.99 3462.48
SXNT
4463.36 4465.08
SX7T
1325.96 1324.44
SX4T
1009.41 1002.99
SXQT
614.12 612.33
SX8T
782.45 791.23
SXIT
3586.37 3546.84
SXAT
3959.76 3974.04
SXDT
348.05 346.3
SXET
1916.18 1902.0
SX6T
1100.16 1095.12
SX3T
308.19 309.79
SXKT
1048.01 1048.11
SXOT
243.93 243.05
SXRT
122.27 121.74
SXMT
520.09 518.55
SX86T
674.63 673.21
SXPT
721.37 720.18
SXFT
802.18 801.91
SXTT
3625.94 3615.99
SXNT
4482.12 4463.36
SX7T
1326.05 1325.96
SX4T
1006.73 1009.41
SXQT
616.19 614.12
SX8T
788.95 782.45
SXIT
3606.73 3586.37
SXAT
3960.85 3959.76
SXDT
348.31 348.05
SXET
1913.59 1916.18
SX6T
1102.24 1100.16
SX3T
308.9 308.19
SXKT
1055.24 1048.01
SXO

✅ Backtest terminé avec succès !

In [83]:
import plotly.express as px
import pandas as pd

money_norm = (final["Money"]/10000000*100) - 100
spx_norm = (final["SXXT"]/final["SXXT"].iloc[0]*100) - 100

df_plot = pd.DataFrame({
    "Date": final["Date"],
    "Portfolio": money_norm,
    "SPX": spx_norm
}).melt(id_vars="Date", var_name="Série", value_name="Évolution en %")

fix = px.line(
    df_plot,
    x="Date",
    y="Évolution en %",
    color="Série",
    color_discrete_map={"SXXT": "red", "Portfolio": "green"},
    title="Comparaison des évolutions en %"
)

fix.update_layout(hovermode="x unified")
fix.show()


In [85]:
AnnualizedDf=final[["Date","SXXT","Money"]]
AnnualizedDf['Date'] = pd.to_datetime(AnnualizedDf['Date'])
AnnualizedDf['Year'] = AnnualizedDf['Date'].dt.year



YearList=AnnualizedDf["Year"].unique()
SPXAnnualized=pd.DataFrame(columns=YearList)
StratAnnualized=pd.DataFrame(columns=YearList)



for year in YearList:
  compteurPerYear=0
  for i in AnnualizedDf.index:
    if AnnualizedDf.loc[i,"Year"]==year:
      if compteurPerYear==0:
        SPXAnnualized.loc[compteurPerYear,year]=AnnualizedDf.loc[i,"SXXT"]
        StratAnnualized.loc[compteurPerYear,year]=AnnualizedDf.loc[i,"Money"]
      else :
        SPXAnnualized.loc[compteurPerYear,year]=AnnualizedDf.loc[i,"SXXT"]/SPXAnnualized.loc[0,year]*100-100
        StratAnnualized.loc[compteurPerYear,year]=AnnualizedDf.loc[i,"Money"]/StratAnnualized.loc[0,year]*100-100
      compteurPerYear+=1

for year in YearList:
  SPXAnnualized.loc[0,year]=SPXAnnualized.loc[0,year]/SPXAnnualized.loc[0,year]*100-100
  StratAnnualized.loc[0,year]=StratAnnualized.loc[0,year]/StratAnnualized.loc[0,year]*100-100



SPXAvg=[]
StratAvg=[]
for i in SPXAnnualized.index:
  sumSPX=0
  sumStrat=0
  for year in SPXAnnualized.columns:
    sumSPX+=SPXAnnualized.loc[i,year]
    sumStrat+=StratAnnualized.loc[i,year]
  SPXAvg.append(sumSPX/len(YearList))
  StratAvg.append(sumStrat/len(YearList))

SPXAnnualized=SPXAnnualized.drop(columns=[2024,2002]) #too much nan
StratAnnualized=StratAnnualized.drop(columns=[2024,2002])

SPXAvg=[]
StratAVG=[]

for i in SPXAnnualized.index:
  sumSPX=0
  sumStrat=0
  for year in SPXAnnualized.columns:
    sumSPX+=SPXAnnualized.loc[i,year]
    sumStrat+=StratAnnualized.loc[i,year]
  SPXAvg.append(sumSPX/len(YearList))
  StratAVG.append(sumStrat/len(YearList))

dff = pd.DataFrame({"Index": (range(len(SPXAvg))),"Portfolio": StratAVG,"SXXT": SPXAvg})


fig = px.line(dff, x="Index", y=["SXXT","Portfolio"], color_discrete_map={"SXXT": "red","Portfolio": "green"})
fig.show()

